In [1]:
import numpy as np
import pandas as pd

from desdeo_problem.testproblems.TestProblems import test_problem_builder

from desdeo_emo.EAs.NIMBUS_EA import NIMBUS_RVEA, NIMBUS_NSGAIII
import plotly.express as ex
from pygmo import fast_non_dominated_sorting as nds
import plotly.graph_objects as go

In [199]:
n_obj = 12
n_var = 19
problem = test_problem_builder(name="DTLZ2", n_of_objectives=n_obj, n_of_variables=n_var)
problem.ideal = np.asarray([0] * n_obj)
problem.nadir = np.asarray([1]*n_obj)

In [200]:
evo_NSGA = NIMBUS_NSGAIII(problem, lattice_resolution=20, n_gen_per_iter=100, n_iterations=1)

In [201]:
plot, pref = evo_NSGA.requests()
print(pref.content["message"])

Provide a reference point worse than to the ideal point and better than the nadir point.
Ideal point: 
f1     0
f2     0
f3     0
f4     0
f5     0
f6     0
f7     0
f8     0
f9     0
f10    0
f11    0
f12    0
Name: ideal, dtype: object
Nadir point: 
f1     1
f2     1
f3     1
f4     1
f5     1
f6     1
f7     1
f8     1
f9     1
f10    1
f11    1
f12    1
Name: nadir, dtype: object
The reference point will be used to create scalarization functions in the preferred region.



In [204]:
response = np.asarray([[0.8]*n_obj])
#response = np.random.rand(1,n_obj)
pref.response = pd.DataFrame(response, columns=pref.content['dimensions_data'].columns)
plot, pref = evo_NSGA.iterate(pref)

In [205]:
columns = problem.get_objective_names()[0] + ['color']
objs = evo_NSGA.population.objectives[nds(evo_NSGA.population.objectives)[0][0]]

objs_col = [[0]] * len(objs)
objs = pd.DataFrame(np.hstack((objs, objs_col)), columns=columns)

resp = pd.DataFrame(np.hstack((response, [[1]])), columns=columns)
ide = pd.DataFrame(np.hstack(([problem.ideal], [[2]])), columns=columns)
nad = pd.DataFrame(np.hstack(([problem.nadir], [[3]])), columns=columns)

fig = ex.parallel_coordinates(
        pd.concat([objs, resp, ide, nad]),
        dimensions=problem.get_objective_names()[0],
        color="color")
fig

In [38]:
np.linalg.norm(evo_NSGA.population.objectives, axis=1).mean()

1.000000002950713

In [39]:
from desdeo_emo.EAs.RVEA import RVEA

In [40]:
ea = RVEA(problem, a_priori=True, interact=True, n_gen_per_iter=100, n_iterations=5)

In [41]:
plot, pref = ea.requests()
print(pref.content["message"])

Provide a reference point worse than or equal to the ideal point:
f1     0
f2     0
f3     0
f4     0
f5     0
f6     0
f7     0
f8     0
f9     0
f10    0
Name: ideal, dtype: object
The reference point will be used to focus the reference vectors towards the preferred region.
If a reference point is not provided, the previous state of the reference vectors is used.
If the reference point is the same as the ideal point, the ideal point, the reference vectors are spread uniformly in the objective space.


In [11]:
while ea.continue_evolution():
    pref.response = pd.DataFrame(response, columns=pref.content['dimensions_data'].columns)
    plot, pref = ea.iterate(pref)

In [12]:
columns = problem.get_objective_names()[0] + ['color']
objs = ea.population.objectives
objs_col = [[0]] * len(objs)
objs = pd.DataFrame(np.hstack((objs, objs_col)), columns=columns)

resp = pd.DataFrame(np.hstack((response, [[1]])), columns=columns)
ide = pd.DataFrame(np.hstack(([problem.ideal], [[2]])), columns=columns)
nad = pd.DataFrame(np.hstack(([problem.nadir], [[3]])), columns=columns)

fig = ex.parallel_coordinates(
        pd.concat([objs, resp, ide, nad]),
        dimensions=problem.get_objective_names()[0],
        color="color")
fig

In [22]:
np.linalg.norm(ea.population.objectives, axis=1).mean()

1.9895318380802383

In [139]:
from scipy.optimize import minimize

In [179]:
def err(x):
    try:
        soln = problem.evaluate(x).objectives
        scalar = evo_NSGA.scalarization_methods[0](soln, response)
        return scalar
    except ValueError as e:
        print(x)
    return(100)

In [180]:
res = minimize(err, np.random.rand(12), bounds=problem.get_variable_bounds())

[0.29551399 0.10019646 0.33959622 0.12983222 0.79120717 0.55817132
 0.81479048 0.48216973 0.79709954 0.         0.23868192 1.00000001]
[0.         0.1001962  0.33959622 0.129832   0.79120757 0.55817136
 0.81479056 0.48216973 0.79709954 0.         0.23967475 1.00000001]
[0.         1.00000001 1.         1.         0.         0.55817859
 0.81480316 0.4821698  0.79710108 0.         0.4403754  1.        ]
[0.         1.         1.00000001 1.         0.         0.55817859
 0.81480316 0.4821698  0.79710108 0.         0.4403754  1.        ]
[0.         1.         1.         1.00000001 0.         0.55817859
 0.81480316 0.4821698  0.79710108 0.         0.4403754  1.        ]
[0.         1.         1.         1.         0.         0.55817859
 0.81480316 0.4821698  0.79710108 0.         0.4403754  1.00000001]
[0.         1.00000001 1.         1.         0.         0.55817372
 0.81479472 0.48216985 0.79710008 0.20593939 0.28276125 1.        ]
[0.         1.         1.00000001 1.         0.        

In [181]:
res.x

array([0.28513418, 0.31604579, 0.37117695, 0.4584867 , 0.59573003,
       0.53378357, 0.77932109, 0.475263  , 0.76558665, 0.43141981,
       0.46192138, 0.55345369])

In [182]:
problem.evaluate(res.x)

EvaluationResults(objectives=array([[0.01786559, 0.0463065 , 0.04591865, 0.18718554, 0.22135279,
        0.40398163, 0.44028541, 0.4402854 , 0.43318932, 0.43696468]]), fitness=array([[0.01786559, 0.0463065 , 0.04591865, 0.18718554, 0.22135279,
        0.40398163, 0.44028541, 0.4402854 , 0.43318932, 0.43696468]]), constraints=None, uncertainity=array([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]]))

In [16]:
from desdeo_emo.othertools.ReferenceVectors import ReferenceVectors

In [17]:
ref = ReferenceVectors(lattice_resolution=7, number_of_objectives=10)

In [18]:
val = ref.values

In [41]:
ex.parallel_coordinates(val)

In [19]:
scalar_data = np.asarray([scalar(val, response) for scalar in evo_NSGA.scalarization_methods]).T

In [66]:
scalar_non_dom

array([[ 0.86031128, -0.09999829, -1.11110366],
       [ 0.90951103, -0.07239135, -1.11110384],
       [ 0.90951103, -0.07239135, -1.11110384],
       [ 0.86031118, -0.09999829, -1.11110308],
       [ 0.69337817, -0.09999796, -1.1111021 ],
       [ 0.90951103, -0.07239135, -1.11110384],
       [ 0.90951103, -0.07239135, -1.11110384],
       [ 0.86031118, -0.09999829, -1.11110308],
       [ 0.86031118, -0.09999829, -1.11110308],
       [ 0.86031128, -0.09999829, -1.11110366],
       [ 0.86031128, -0.09999829, -1.11110366],
       [ 0.90951103, -0.07239135, -1.11110384],
       [ 0.90951103, -0.07239135, -1.11110384]])

In [134]:
fig = ex.scatter_3d(
    x=scalar_data[:,0],
    y=scalar_data[:,1],
    z=scalar_data[:,2],
    size_max=5,
    size=[2]*len(scalar_data),
    labels="All")
scalar_non_dom = scalar_data[nds(scalar_data)[0][0]]
fig.add_trace(go.Scatter3d(x=scalar_non_dom[:,0],
        y=scalar_non_dom[:,1],
        z=scalar_non_dom[:,2],
        name="preferred from generated",
        mode='markers',
        marker=dict(
            size=2,
            opacity=0.8
        )))
nimbea = evo_NSGA.population.objectives
nimbea = np.asarray([scalar(nimbea, response) for scalar in evo_NSGA.scalarization_methods]).T

fig.add_trace(go.Scatter3d(x=scalar_non_dom[:,0],
        y=nimbea[:,1],
        z=nimbea[:,2],
        name="Nimbus-EA",
        mode='markers',
        marker=dict(
            size=2,
            opacity=0.8
        )))

rvea = ea.population.objectives
rvea = np.asarray([scalar(rvea, response) for scalar in evo_NSGA.scalarization_methods]).T

fig.add_trace(go.Scatter3d(x=scalar_non_dom[:,0],
        y=rvea[:,1],
        z=rvea[:,2],
        name="iRVEA",
        mode='markers',
        marker=dict(
            size=2,
            opacity=0.8
        )))

In [20]:
fig = ex.scatter(
    x=scalar_data[:,0],
    y=scalar_data[:,1],
    size_max=5,
    size=[2]*len(scalar_data),
    labels="All")
scalar_non_dom = scalar_data[nds(scalar_data)[0][0]]
fig.add_trace(go.Scatter(x=scalar_non_dom[:,0],
        y=scalar_non_dom[:,1],
        name="preferred from generated",
        mode='markers',
        marker=dict(
            size=2,
            opacity=0.8
        )))
nimbea = evo_NSGA.population.objectives
nimbea = np.asarray([scalar(nimbea, response) for scalar in evo_NSGA.scalarization_methods]).T

fig.add_trace(go.Scatter(x=scalar_non_dom[:,0],
        y=nimbea[:,1],
        name="Nimbus-EA",
        mode='markers',
        marker=dict(
            size=4,
            opacity=0.8
        )))

rvea = ea.population.objectives
rvea = np.asarray([scalar(rvea, response) for scalar in evo_NSGA.scalarization_methods]).T

fig.add_trace(go.Scatter(x=scalar_non_dom[:,0],
        y=rvea[:,1],
        name="iRVEA",
        mode='markers',
        marker=dict(
            size=4,
            opacity=0.8
        )))

In [62]:
non_dom = nds(scalar_data)[0][0]

In [21]:
scalar_non_dom

array([[-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.07239135, -1.11110505],
       [-0.07239135, -1.11110505],
       [-0.07239135, -1.11110505],
       [-0.07239135, -1.11110505],
       [-0.07239135, -1.11110505],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829, -1.11110366],
       [-0.09999829,

In [63]:
val_non_dom = [[0]] * len(val[non_dom,:])
val_non_dom = pd.DataFrame(np.hstack((val[non_dom,:], val_non_dom)), columns=columns)
ex.parallel_coordinates(
        pd.concat([val_non_dom, resp, ide, nad]),
        dimensions=problem.get_objective_names()[0],
        color="color")

In [65]:
non_dom.shape

(13,)